In [1]:
from researchdataset import VideoDataset
video_directory = "C:/Users/vladi/RP/Research/IR_videos"  # Replace with your directory
dataset = VideoDataset(video_directory, transform=None, frame_skip=240)


Loading videos:  12%|█▎        | 1/8 [00:59<06:54, 59.17s/it]

In [3]:
import sys
import os
import os.path as osp
import argparse
import numpy as np
import cv2
import json
import torch
from glob import glob
from tqdm import tqdm
import torchvision.transforms as transforms
from torch.nn.parallel.data_parallel import DataParallel
import torch.backends.cudnn as cudnn
ir_image_dir = r"C:\Users\vladi\RP\our_hands_dataset_labeled_previews\IR"
ir_image_paths = glob(osp.join(ir_image_dir, "*.jpg"))  # Assuming images are in .jpg forma
# Create a custom dataset for your infrared images
# Create a custom dataset for your infrared images
class InfraredDataset(torch.utils.data.Dataset):
    def __init__(self, image_paths, transform=None):
        self.image_paths = image_paths
        self.transform = transform

    def __len__(self):
        return len(self.image_paths)

    def __getitem__(self, idx):
        img_path = self.image_paths[idx]

        # Load and preprocess the image using InterWild's functions
        original_img = load_img(img_path)
        img_height, img_width = original_img.shape[:2]
        bbox = [0, 0, img_width, img_height]  # Use the entire image as the initial bbox
        bbox = process_bbox(bbox, img_width, img_height)
        img, img2bb_trans, bb2img_trans = generate_patch_image(original_img, bbox, 1.0, 0.0, False, cfg.input_img_shape)

        if self.transform:
            img = self.transform(img.astype(np.float32)) / 255
        
        return img

# Define transformations (match demo.py preprocessing)
transform = transforms.Compose([
    transforms.ToTensor(),
])

# Create dataset and dataloader
ir_dataset = InfraredDataset(ir_image_paths, transform=transform)

In [4]:
dataset_loader = torch.utils.data.DataLoader(dataset, batch_size=1, shuffle=False, num_workers=0)


In [25]:
sys.path.insert(0, osp.join('..', 'main'))
sys.path.insert(0, osp.join('..', 'data'))
sys.path.insert(0, osp.join('..', 'common'))
from config import cfg
from model import get_model
from utils.preprocessing import load_img, process_bbox, generate_patch_image, get_iou
from utils.vis import vis_keypoints_with_skeleton, save_obj, render_mesh_orthogonal
from utils.mano import mano
cfg.set_args("0")
cudnn.benchmark = True

model_path = './snapshot_6.pth'
assert osp.exists(model_path), 'Cannot find model at ' + model_path
print('Load checkpoint from {}'.format(model_path))
model = get_model('test')
model = DataParallel(model).cuda()
ckpt = torch.load(model_path)
model.load_state_dict(ckpt['network'], strict=False)
model.eval()


>>> Using GPU: 0
Load checkpoint from ./snapshot_6.pth


C:\Users\vladi\AppData\Local\Temp\ipykernel_33032\344236309.py:17: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  ckpt = torch.load(model_path)


DataParallel(
  (module): Model(
    (body_backbone): ResNetBackbone(
      (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace=True)
      (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
      (layer1): Sequential(
        (0): Bottleneck(
          (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
          (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn3): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          (relu

In [6]:
def preprocess_image(image_array):
    # Process bbox
    bbox = [0, 0, image_array.shape[1], image_array.shape[0]]  # Use entire image
    bbox = process_bbox(bbox, image_array.shape[1], image_array.shape[0])
    
    # Generate patch image
    img, img2bb_trans, bb2img_trans = generate_patch_image(image_array, bbox, 1.0, 0.0, False, cfg.input_img_shape)
    
    # Transform and normalize
    transform = transforms.ToTensor()
    img = transform(img.astype(np.float32))/255
    img = img.cuda()
    
    return img


In [7]:
for i in tqdm(range(len(dataset.data))):
   processed_frame = preprocess_image(dataset.data[i])
   if processed_frame is not None:
       dataset.data[i] = processed_frame

100%|██████████| 826/826 [00:15<00:00, 54.34it/s] 


In [19]:
from performAdaBN import perform_adabn_with_hook
import importlib
importlib.import_module('performAdaBN')

<module 'performAdaBN' from 'c:\\Users\\vladi\\RP\\InterWild\\demo\\performAdaBN.py'>

In [26]:
import torch
import torch.nn as nn
from torch.utils.data import DataLoader
from tqdm import tqdm
from adabn_utils import compute_bn_stats, replace_bn_stats, BatchNormStatHook
from functools import partial
model.eval()
hook = BatchNormStatHook()

# Register hooks for all BatchNorm layers
with torch.no_grad():

    for name, module in model.named_modules():
        if isinstance(module, torch.nn.BatchNorm2d):
            module.train()
            hook_handle = module.register_forward_hook(partial(hook, name=name))
            hook.hooks.append(hook_handle)
            
    # Process target domain data
    device = next(model.parameters()).device
    for data in dataset_loader:
        inputs = data[0].to(device)
  
        model_inputs = {'img': inputs}
        targets = {}
        meta_info = {}
        
        # Forward pass to accumulate statistics
        print("inputs.shape")
        print(inputs.shape)
        model(model_inputs, targets, meta_info, "test")

inputs.shape
torch.Size([1, 3, 512, 384])
torch.Size([1, 64, 128, 96])
torch.Size([64, 128, 96])
torch.Size([1, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([1, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([1, 256, 64, 48])
torch.Size([256, 64, 48])
torch.Size([1, 256, 64, 48])
torch.Size([256, 64, 48])
torch.Size([1, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([1, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([1, 256, 64, 48])
torch.Size([256, 64, 48])
torch.Size([1, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([1, 64, 64, 48])
torch.Size([64, 64, 48])
torch.Size([1, 256, 64, 48])
torch.Size([256, 64, 48])
torch.Size([1, 128, 64, 48])
torch.Size([128, 64, 48])
torch.Size([1, 128, 32, 24])
torch.Size([128, 32, 24])
torch.Size([1, 512, 32, 24])
torch.Size([512, 32, 24])
torch.Size([1, 512, 32, 24])
torch.Size([512, 32, 24])
torch.Size([1, 128, 32, 24])
torch.Size([128, 32, 24])
torch.Size([1, 128, 32, 24])
torch.Size([128, 32, 24])
torch.Size([1, 512, 32, 24])
torch.

c:\Users\vladi\.pyenv\pyenv-win\versions\3.10.11\lib\site-packages\torch\functional.py:534: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at C:\actions-runner\_work\pytorch\pytorch\builder\windows\pytorch\aten\src\ATen\native\TensorShape.cpp:3596.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]


torch.Size([1, 64, 64, 64])
torch.Size([64, 64, 64])
torch.Size([1, 64, 64, 64])
torch.Size([64, 64, 64])
torch.Size([1, 64, 64, 64])
torch.Size([64, 64, 64])
torch.Size([1, 64, 64, 64])
torch.Size([64, 64, 64])
torch.Size([1, 64, 64, 64])
torch.Size([64, 64, 64])
torch.Size([1, 128, 32, 32])
torch.Size([128, 32, 32])
torch.Size([1, 128, 32, 32])
torch.Size([128, 32, 32])
torch.Size([1, 128, 32, 32])
torch.Size([128, 32, 32])
torch.Size([1, 128, 32, 32])
torch.Size([128, 32, 32])
torch.Size([1, 128, 32, 32])
torch.Size([128, 32, 32])
torch.Size([1, 256, 16, 16])
torch.Size([256, 16, 16])
torch.Size([1, 256, 16, 16])
torch.Size([256, 16, 16])
torch.Size([1, 256, 16, 16])
torch.Size([256, 16, 16])
torch.Size([1, 256, 16, 16])
torch.Size([256, 16, 16])
torch.Size([1, 256, 16, 16])
torch.Size([256, 16, 16])
torch.Size([1, 512, 8, 8])
torch.Size([512, 8, 8])
torch.Size([1, 512, 8, 8])
torch.Size([512, 8, 8])
torch.Size([1, 512, 8, 8])
torch.Size([512, 8, 8])
torch.Size([1, 512, 8, 8])
torch

In [27]:
for hook_handle in hook.hooks:
    hook_handle.remove()

for layer_name, stats in hook.bn_stats.items():
    # Average the accumulated statistics
    mean = stats['mean'] / stats['count']
    var = stats['var'] / stats['count']
    hook.bn_stats[layer_name] = {'mean': mean, 'var': var}

In [28]:
replace_bn_stats(model, hook.bn_stats)

Before Apply module.body_backbone.bn1---------------------------------------
Running Mean: tensor([-9.4112e-02,  2.6843e-01, -4.4941e-01, -3.7856e-03, -8.8801e-03,
        -5.9483e-02, -5.7886e-03,  9.7712e-03, -2.3807e-02, -9.8136e-02,
        -1.5991e-02,  7.0175e-01, -6.5850e-03,  4.2185e-07, -2.6900e-02,
        -3.9775e-03, -1.1486e-01, -1.9856e-02, -5.4647e-03,  1.0271e-02,
        -1.8541e-02, -2.7800e-02, -1.8182e-02, -2.4609e-01, -6.6406e-02,
        -4.8285e-01, -4.3424e-02, -2.8302e-02, -2.9838e-02, -4.0225e-01,
         1.9108e-02,  4.0956e-01,  9.6241e-01, -1.9371e-03,  2.2461e-02,
         1.1339e-01, -2.4845e-02,  1.2691e-01, -1.4139e-02, -4.0166e-03,
         7.5606e-01, -4.5348e-03,  1.0298e+00, -4.3476e-01, -1.1286e+00,
        -3.7557e-04, -1.1238e-02, -1.5573e-01,  4.9032e-01, -2.0562e-02,
        -3.6531e-02, -8.6241e-04, -8.8441e-01, -9.5232e-03, -3.0957e-02,
         1.6942e-01,  7.3600e-02,  2.2345e-01, -6.8382e-01,  1.2089e-01,
         8.7461e-03, -4.7877e-02,

In [44]:
class OutputCopyHook(object):
    def __init__(self):
        self.outputs = {}  # Dictionary to store layer outputs
        self.hooks = []

    def __call__(self, module, input, output, name):
        """
        Hook function called during the forward pass of layers.
        Args:
            module (nn.Module): The layer.
            input (torch.Tensor): Input tensor to the layer.
            output (torch.Tensor): Output tensor from the layer.
            name (str): Name of the layer.
        """
        if name not in self.outputs:
            self.outputs[name] = []
        self.outputs[name].append(output.detach().clone())

    def unhook(self):
        """Remove all hooks."""
        for hook in self.hooks:
            hook.remove()
        self.hooks = []


In [47]:
model.eval()
copyhook = OutputCopyHook()

# Register hooks only for BatchNorm layers
i = 0
with torch.no_grad():
    for name, module in model.named_modules():
        if isinstance(module, nn.BatchNorm2d):
            if i % 4 != 0:
                continue
            hook_handle = module.register_forward_hook(partial(copyhook, name=name))
            copyhook.hooks.append(hook_handle)
            i += 1
    
    # Process data
    device = next(model.parameters()).device
    for data in dataset_loader:
        inputs = data[0].to(device)
        
        # Forward pass
        model_inputs = {'img': inputs}
        targets = {}
        meta_info = {}
        model(model_inputs, targets, meta_info, "test")
        
        # We only need one batch to capture the outputs
    
    # Clean up hooks
    copyhook.unhook()

OutOfMemoryError: CUDA out of memory. Tried to allocate 22.00 MiB. GPU 0 has a total capacity of 8.00 GiB of which 0 bytes is free. Of the allocated memory 10.59 GiB is allocated by PyTorch, and 62.79 MiB is reserved by PyTorch but unallocated. If reserved but unallocated memory is large try setting PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True to avoid fragmentation.  See documentation for Memory Management  (https://pytorch.org/docs/stable/notes/cuda.html#environment-variables)

In [46]:
len(copyhook.outputs['module.body_backbone.bn1'])

1